In [ ]:
# Importing the OpenAI library
import openai
# Include the api bas and the api key
openai.api_base = "https://openai.vocareum.com/v1"
openai.api_key = "" # Replace with your actual API key

In [5]:
# Creating a prompt
prompt = """
Question: When did Russia invade Ukraine?
Answer: 
"""

In [6]:
answer = openai.Completion.create(
    model="gpt-3.5-turbo-instruct",
    prompt=prompt
)

In [7]:
# Extracting the model's response
answer

<OpenAIObject text_completion id=cmpl-CD4c1qbFyYdtAwEofBDGsSe5gFJs7 at 0x71207811f130> JSON: {
  "choices": [
    {
      "finish_reason": "stop",
      "index": 0,
      "logprobs": null,
      "text": "Russia invaded Ukraine in February 2014."
    }
  ],
  "created": 1757232029,
  "id": "cmpl-CD4c1qbFyYdtAwEofBDGsSe5gFJs7",
  "model": "gpt-3.5-turbo-instruct:20230824-v2",
  "object": "text_completion",
  "usage": {
    "completion_tokens": 9,
    "prompt_tokens": 12,
    "total_tokens": 21
  }
}

In [8]:
answer["choices"][0]["text"]

'Russia invaded Ukraine in February 2014.'

In [17]:
# Gathering data from wikipedia for the year 2022
import requests

params = {
    "action": "query", 
    "prop": "extracts",
    "exlimit": 1,
    "titles": "2022",
    "explaintext": 1,
    "formatversion": 2,
    "format": "json"
}

headers = {"User-Agent": "GenerativeAIProject/1.0 (sriramramesh1698@gmail.com)"}
resp = requests.get("https://en.wikipedia.org/w/api.php", params=params, headers=headers)

In [18]:
print(resp.text) 

{"batchcomplete":true,"query":{"pages":[{"pageid":52412,"ns":0,"title":"2022","extract":"2022 (MMXXII) was a common year starting on Saturday of the Gregorian calendar, the 2022nd year of the Common Era (CE) and Anno Domini (AD) designations, the 22nd  year of the 3rd millennium and the 21st century, and the  3rd   year of the 2020s decade.  \nThe year began with another wave in the COVID-19 pandemic, with Omicron spreading rapidly and becoming the dominant variant of the SARS-CoV-2 virus worldwide. Tracking a decrease in cases and deaths, 2022 saw the removal of most COVID-19 restrictions and the reopening of international borders in the vast majority of countries, while the global rollout of COVID-19 vaccines continued. The global economic recovery from the pandemic continued, though many countries experienced an ongoing inflation surge; in response, many central banks raised their interest rates to landmark levels. The world population reached eight billion people in 2022. The year 

In [19]:
resp.json()

{'batchcomplete': True,
 'query': {'pages': [{'pageid': 52412,
    'ns': 0,
    'title': '2022',
    'extract': '2022 (MMXXII) was a common year starting on Saturday of the Gregorian calendar, the 2022nd year of the Common Era (CE) and Anno Domini (AD) designations, the 22nd  year of the 3rd millennium and the 21st century, and the  3rd   year of the 2020s decade.  \nThe year began with another wave in the COVID-19 pandemic, with Omicron spreading rapidly and becoming the dominant variant of the SARS-CoV-2 virus worldwide. Tracking a decrease in cases and deaths, 2022 saw the removal of most COVID-19 restrictions and the reopening of international borders in the vast majority of countries, while the global rollout of COVID-19 vaccines continued. The global economic recovery from the pandemic continued, though many countries experienced an ongoing inflation surge; in response, many central banks raised their interest rates to landmark levels. The world population reached eight billion p

In [20]:
response_dict = resp.json()

In [22]:
response_dict["query"]["pages"][0]["extract"].split("\n")

['2022 (MMXXII) was a common year starting on Saturday of the Gregorian calendar, the 2022nd year of the Common Era (CE) and Anno Domini (AD) designations, the 22nd  year of the 3rd millennium and the 21st century, and the  3rd   year of the 2020s decade.  ',
 'The year began with another wave in the COVID-19 pandemic, with Omicron spreading rapidly and becoming the dominant variant of the SARS-CoV-2 virus worldwide. Tracking a decrease in cases and deaths, 2022 saw the removal of most COVID-19 restrictions and the reopening of international borders in the vast majority of countries, while the global rollout of COVID-19 vaccines continued. The global economic recovery from the pandemic continued, though many countries experienced an ongoing inflation surge; in response, many central banks raised their interest rates to landmark levels. The world population reached eight billion people in 2022. The year also witnessed numerous natural disasters, including two devastating Atlantic hurric

In [30]:
import pandas as pd

In [31]:
df = pd.DataFrame()
df["text"] = response_dict["query"]["pages"][0]["extract"].split("\n")

In [32]:
df

text
0    2022 (MMXXII) was a common year starting on Sa...
1    The year began with another wave in the COVID-...
2    2022 was also dominated by wars and armed conf...
3                                                     
4                                                     
..                                                 ...
287                                   == References ==
288                                                   
289                                                   
290                               == External links ==
291         Media related to 2022 at Wikimedia Commons

[292 rows x 1 columns]

In [33]:
df = df[df["text"].str.len() > 0]
df

text
0    2022 (MMXXII) was a common year starting on Sa...
1    The year began with another wave in the COVID-...
2    2022 was also dominated by wars and armed conf...
5                                      == Conflicts ==
7    The ongoing Russian invasion of Ukraine escala...
..                                                 ...
281                            == Births and deaths ==
284                                 == Nobel Prizes ==
287                                   == References ==
290                               == External links ==
291         Media related to 2022 at Wikimedia Commons

[253 rows x 1 columns]

In [34]:
df = df[-df["text"].str.startswith("==")]
df

text
0    2022 (MMXXII) was a common year starting on Sa...
1    The year began with another wave in the COVID-...
2    2022 was also dominated by wars and armed conf...
7    The ongoing Russian invasion of Ukraine escala...
14                                           January 1
..                                                 ...
272  December 24 – 2022 Fijian general election: Th...
273  December 29 – Brazilian football legend Pelé d...
274  December 31 – Former Pope Benedict XVI dies at...
278  The world population was estimated to have rea...
291         Media related to 2022 at Wikimedia Commons

[234 rows x 1 columns]

In [35]:
from dateutil.parser import parse

# Clean up text to remove empty lines and headings
df = df[(df["text"].str.len() > 0) & (~df["text"].str.startswith("=="))]

# In some cases dates are used as headings instead of being part of the
# text sample; adjust so dated text samples start with dates
prefix = ""
for (i, row) in df.iterrows():
    # If the row already has " - ", it already has the needed date prefix
    if " – " not in row["text"]:
        try:
            # If the row's text is a date, set it as the new prefix
            parse(row["text"])
            prefix = row["text"]
        except:
            # If the row's text isn't a date, add the prefix
            row["text"] = prefix + " – " + row["text"]
df = df[df["text"].str.contains(" – ")].reset_index(drop=True)

In [36]:
df

text
0     – 2022 (MMXXII) was a common year starting on...
1     – The year began with another wave in the COV...
2     – 2022 was also dominated by wars and armed c...
3     – The ongoing Russian invasion of Ukraine esc...
4     January 1 – France takes over the Presidency ...
..                                                 ...
202  December 24 – 2022 Fijian general election: Th...
203  December 29 – Brazilian football legend Pelé d...
204  December 31 – Former Pope Benedict XVI dies at...
205  December 7 – The world population was estimate...
206  December 7 –  Media related to 2022 at Wikimed...

[207 rows x 1 columns]

In [37]:
df.reset_index(inplace=True, drop=True)
df

text
0     – 2022 (MMXXII) was a common year starting on...
1     – The year began with another wave in the COV...
2     – 2022 was also dominated by wars and armed c...
3     – The ongoing Russian invasion of Ukraine esc...
4     January 1 – France takes over the Presidency ...
..                                                 ...
202  December 24 – 2022 Fijian general election: Th...
203  December 29 – Brazilian football legend Pelé d...
204  December 31 – Former Pope Benedict XVI dies at...
205  December 7 – The world population was estimate...
206  December 7 –  Media related to 2022 at Wikimed...

[207 rows x 1 columns]

In [ ]:
df.to_csv("data/text.csv", index=False)

In [41]:
EMBEDDING_MODEL = "text-embedding-ada-002"
embedding_response = openai.Embedding.create(
    input=df["text"].tolist(),
    model=EMBEDDING_MODEL
)

In [42]:
type(embedding_response)

openai.openai_object.OpenAIObject

In [43]:
embedding_response.keys()

dict_keys(['object', 'data', 'model', 'usage'])

In [45]:
embedding_response["data"][0]["embedding"].__len__()

1536

In [46]:
embeddings = [data["embedding"] for data in embedding_response["data"]]
embeddings

[[9.842545114224777e-05,
  -0.01795295812189579,
  -0.017136914655566216,
  -0.012221821583807468,
  -0.009585373103618622,
  -0.00121700344607234,
  -0.00838014017790556,
  0.01324501447379589,
  -0.022497693076729774,
  -0.0020746339578181505,
  0.03000529482960701,
  0.024418534711003304,
  -0.018919656053185463,
  -0.0168607160449028,
  -0.0021264213137328625,
  0.004579260013997555,
  0.018517911434173584,
  -0.004588675685226917,
  0.02124224230647087,
  0.009641868993639946,
  0.002306892303749919,
  0.00979252252727747,
  -0.002088757697492838,
  -0.013948068022727966,
  0.009874126873910427,
  0.017500996589660645,
  0.00454159639775753,
  -0.005028083920478821,
  0.035855699330568314,
  -0.022962210699915886,
  -0.00022343115415424109,
  -0.010884765535593033,
  -0.014977538026869297,
  -0.016948597505688667,
  0.0034776011016219854,
  -0.028875388205051422,
  -0.013835077174007893,
  -0.0017874492332339287,
  0.004852320533245802,
  -0.012309703044593334,
  0.012008395045995

In [50]:
df["embeddings"] = embeddings
df

text  \
0     – 2022 (MMXXII) was a common year starting on...   
1     – The year began with another wave in the COV...   
2     – 2022 was also dominated by wars and armed c...   
3     – The ongoing Russian invasion of Ukraine esc...   
4     January 1 – France takes over the Presidency ...   
..                                                 ...   
202  December 24 – 2022 Fijian general election: Th...   
203  December 29 – Brazilian football legend Pelé d...   
204  December 31 – Former Pope Benedict XVI dies at...   
205  December 7 – The world population was estimate...   
206  December 7 –  Media related to 2022 at Wikimed...   

                                            embeddings  
0    [9.842545114224777e-05, -0.01795295812189579, ...  
1    [-0.0046722241677343845, -0.02001906745135784,...  
2    [-0.009640222415328026, -0.01530236192047596, ...  
3    [-0.014610757119953632, -0.00763713987544179, ...  
4    [0.03014434315264225, -0.010520173236727715, -...  
..                                                 ...  
202  [-0.011664693243801594, -0.009389596059918404,...  
203  [-0.007616548798978329, 0.0040343510918319225,...  
204  [0.02361743524670601, 0.007801263593137264, -0...  
205  [-0.0041075884364545345, -0.014412812888622284...  
206  [-0.010555346496403217, -0.018195774406194687,...  

[207 rows x 2 columns]

In [53]:
df.to_csv("data/embeddings.csv")

In [56]:
# Semantic text search with Unsupervised Machine Learning
import numpy as np
df = pd.read_csv("data/embeddings.csv", index_col=0)
df["embeddings"] = df["embeddings"].apply(eval).apply(np.array)
df

text  \
0     – 2022 (MMXXII) was a common year starting on...   
1     – The year began with another wave in the COV...   
2     – 2022 was also dominated by wars and armed c...   
3     – The ongoing Russian invasion of Ukraine esc...   
4     January 1 – France takes over the Presidency ...   
..                                                 ...   
202  December 24 – 2022 Fijian general election: Th...   
203  December 29 – Brazilian football legend Pelé d...   
204  December 31 – Former Pope Benedict XVI dies at...   
205  December 7 – The world population was estimate...   
206  December 7 –  Media related to 2022 at Wikimed...   

                                            embeddings  
0    [9.842545114224777e-05, -0.01795295812189579, ...  
1    [-0.0046722241677343845, -0.02001906745135784,...  
2    [-0.009640222415328026, -0.01530236192047596, ...  
3    [-0.014610757119953632, -0.00763713987544179, ...  
4    [0.03014434315264225, -0.010520173236727715, -...  
..                                                 ...  
202  [-0.011664693243801594, -0.009389596059918404,...  
203  [-0.007616548798978329, 0.0040343510918319225,...  
204  [0.02361743524670601, 0.007801263593137264, -0...  
205  [-0.0041075884364545345, -0.014412812888622284...  
206  [-0.010555346496403217, -0.018195774406194687,...  

[207 rows x 2 columns]

In [61]:
df["embeddings"]

0      [9.842545114224777e-05, -0.01795295812189579, ...
1      [-0.0046722241677343845, -0.02001906745135784,...
2      [-0.009640222415328026, -0.01530236192047596, ...
3      [-0.014610757119953632, -0.00763713987544179, ...
4      [0.03014434315264225, -0.010520173236727715, -...
                             ...                        
202    [-0.011664693243801594, -0.009389596059918404,...
203    [-0.007616548798978329, 0.0040343510918319225,...
204    [0.02361743524670601, 0.007801263593137264, -0...
205    [-0.0041075884364545345, -0.014412812888622284...
206    [-0.010555346496403217, -0.018195774406194687,...
Name: embeddings, Length: 207, dtype: object

In [64]:
df["embeddings"][0].__len__()

1536

In [65]:
question = "When did Russia invade Ukraine?"

In [66]:
from openai.embeddings_utils import get_embedding
question_embedding = get_embedding(
    question,
    engine=EMBEDDING_MODEL
)
question_embedding

[0.0016044961521402001,
 -0.019282648339867592,
 0.0034815892577171326,
 -0.013990121893584728,
 -0.02527659200131893,
 0.001979914726689458,
 -0.013735060580074787,
 -0.024689950048923492,
 -0.013352468609809875,
 -0.02120836079120636,
 0.022394398227334023,
 0.02462618611752987,
 -0.009048305451869965,
 -0.011873112060129642,
 -0.006309583317488432,
 -0.010489403270184994,
 0.010610557161271572,
 -0.003959829453378916,
 0.03336204215884209,
 -0.01868325285613537,
 -0.01435996126383543,
 -0.01624741591513157,
 0.0033349287696182728,
 0.0013040017802268267,
 -0.014831825159490108,
 0.006733622867614031,
 0.013735060580074787,
 -0.029102513566613197,
 0.015431219711899757,
 -0.014449232257902622,
 -0.01113981008529663,
 -0.022815249860286713,
 -0.020494189113378525,
 -0.016158144921064377,
 -0.035121966153383255,
 -0.03239280730485916,
 0.009150330908596516,
 -0.009367132559418678,
 0.015048626810312271,
 -0.004061853978782892,
 0.009507416747510433,
 0.017892561852931976,
 -0.004600671

In [67]:
from openai.embeddings_utils import distances_from_embeddings

In [68]:
distances = distances_from_embeddings(question_embedding, df["embeddings"].tolist(), distance_metric="cosine")


In [69]:
distances

[0.2908903215204931,
 0.28037983290064616,
 0.18546776045836844,
 0.13044685761232355,
 0.2523468115789561,
 0.28957109522315405,
 0.2617111353642082,
 0.23050001805686615,
 0.21792237755346433,
 0.17787214491359027,
 0.2620340983673952,
 0.2628402300909589,
 0.2869744462731052,
 0.27513600403919924,
 0.2539654806741136,
 0.2644186717689673,
 0.23337581312596367,
 0.2535144892914569,
 0.2624402543003236,
 0.23036679700896678,
 0.27162722260906624,
 0.25524698582109795,
 0.2466777910946618,
 0.20034441173790563,
 0.2612748624294866,
 0.25013022290545506,
 0.25325453318915114,
 0.2830607868793723,
 0.12126915626485624,
 0.24558555684098093,
 0.14679578561723805,
 0.13761501045102553,
 0.1384582557209345,
 0.17967408441586097,
 0.1809651214473602,
 0.2714045799021372,
 0.12599167624683005,
 0.1563881272621146,
 0.19412455541450535,
 0.16546418176948996,
 0.12621390078362094,
 0.10925132244819802,
 0.13494332221177852,
 0.15473830383081266,
 0.14711381348989971,
 0.24188597651865362,
 0.21

In [70]:
df["distances"] = distances
df

text  \
0     – 2022 (MMXXII) was a common year starting on...   
1     – The year began with another wave in the COV...   
2     – 2022 was also dominated by wars and armed c...   
3     – The ongoing Russian invasion of Ukraine esc...   
4     January 1 – France takes over the Presidency ...   
..                                                 ...   
202  December 24 – 2022 Fijian general election: Th...   
203  December 29 – Brazilian football legend Pelé d...   
204  December 31 – Former Pope Benedict XVI dies at...   
205  December 7 – The world population was estimate...   
206  December 7 –  Media related to 2022 at Wikimed...   

                                            embeddings  distances  
0    [9.842545114224777e-05, -0.01795295812189579, ...   0.290890  
1    [-0.0046722241677343845, -0.02001906745135784,...   0.280380  
2    [-0.009640222415328026, -0.01530236192047596, ...   0.185468  
3    [-0.014610757119953632, -0.00763713987544179, ...   0.130447  
4    [0.03014434315264225, -0.010520173236727715, -...   0.252347  
..                                                 ...        ...  
202  [-0.011664693243801594, -0.009389596059918404,...   0.247974  
203  [-0.007616548798978329, 0.0040343510918319225,...   0.287805  
204  [0.02361743524670601, 0.007801263593137264, -0...   0.293079  
205  [-0.0041075884364545345, -0.014412812888622284...   0.264025  
206  [-0.010555346496403217, -0.018195774406194687,...   0.278347  

[207 rows x 3 columns]

In [71]:
df.to_csv("data/distances.csv")

In [74]:
df.sort_values("distances").to_csv("data/sorted_distances.csv")

In [75]:
import tiktoken

In [76]:
tokenizer = tiktoken.get_encoding("cl100k_base")
tokenizer

<Encoding 'cl100k_base'>

In [77]:
len(tokenizer.encode(question))

6

In [79]:
# Composing a custom text prompt
# Count the number of tokens in the prompt template and question
prompt_template = """
Answer the question based on the context below, and if the question
can't be answered based on the context, say "I don't know"

Context: 

{}

---

Question: {}
Answer:"""

In [80]:
current_token_count = len(tokenizer.encode(prompt_template)) + \
                            len(tokenizer.encode(question))

In [81]:
current_token_count

47

In [83]:
MAX_TOKEN_COUNT = 1000 
context = []
df = pd.read_csv("data/sorted_distances.csv", index_col=0)
df

text  \
41   March 2 – Russian invasion of Ukraine: Russia ...   
65   April 3 – Russian invasion of Ukraine: As Russ...   
182  November 11 – Russian invasion of Ukraine: Ukr...   
153  September 21 – Russian invasion of Ukraine: Fo...   
93   May 16 – Russian invasion of Ukraine: The Sieg...   
..                                                 ...   
204  December 31 – Former Pope Benedict XVI dies at...   
181  November 11 – The cryptocurrency exchange FTX,...   
190  November 20 – 2022 Nepalese general election: ...   
67   April 4 – The Intergovernmental Panel on Clima...   
84   April 30 – The Cebu–Cordova Link Expressway, l...   

                                            embeddings  distances  
41   [ 0.00074991 -0.01837988  0.01266085 ...  0.01...   0.109251  
65   [-0.01216491 -0.0124051   0.00537814 ...  0.01...   0.111409  
182  [-0.01200405 -0.01397524  0.0164645  ...  0.02...   0.115497  
153  [-0.025673   -0.02207111  0.01325799 ...  0.00...   0.116909  
93   [-0.01828887 -0.00646825  0.01106285 ...  0.00...   0.119213  
..                                                 ...        ...  
204  [ 0.02361744  0.00780126 -0.01283162 ...  0.00...   0.293079  
181  [ 2.40485440e-03 -2.53873281e-02 -1.55855832e-...   0.294182  
190  [-0.00423768 -0.00069555 -0.00154808 ... -0.00...   0.295616  
67   [-0.01047762 -0.01639136  0.0026869  ...  0.01...   0.298530  
84   [-0.00822132 -0.00302293 -0.00673421 ... -0.01...   0.301355  

[207 rows x 3 columns]

In [84]:
for text in df["text"].values:
    token_count = len(tokenizer.encode(text))
    if current_token_count + token_count <= MAX_TOKEN_COUNT:
        context.append(text)
        current_token_count += token_count
    else:
        break

In [85]:
print(prompt_template.format("\n\n###\n\n".join(context), question))


Answer the question based on the context below, and if the question
can't be answered based on the context, say "I don't know"

Context: 

March 2 – Russian invasion of Ukraine: Russia captures its first large city, the Black Sea port of Kherson, as shelling intensifies across many parts of Ukraine, including civilian areas.

###

April 3 – Russian invasion of Ukraine: As Russia's forces retreat from areas near Kyiv, it is accused by Ukraine of war crimes, amid mounting evidence of indiscriminate civilian killings, including the Bucha massacre.

###

November 11 – Russian invasion of Ukraine: Ukrainian forces recapture Kherson, the only regional capital to be taken by Russia since the start of the war.

###

September 21 – Russian invasion of Ukraine: Following a major counteroffensive by Ukraine in the east of the country, Putin announces a partial mobilisation of Russia and threatens nuclear retaliation, saying "this is not a bluff".

###

May 16 – Russian invasion of Ukraine: The S

In [86]:
# Querying a Completion model with context
answer = openai.Completion.create(
    model="gpt-3.5-turbo-instruct",
    prompt=prompt_template.format("\n\n###\n\n".join(context), question))["choices"][0]["text"].strip()

In [87]:
answer

'February 21 – February 24'